In [48]:
import torch
from torch.utils.data import Dataset
import json
import os
import torch.nn as nn
import torch.nn.functional as func
from torch.utils.data import DataLoader
import torch.optim as optim
from os.path import expanduser
import splitfolders
import shutil
import glob
import numpy as np
from sklearn.model_selection import train_test_split

In [49]:
class KpVelDataset(Dataset):
    def __init__(self, json_folder):
        super(KpVelDataset, self).__init__()
        self.data = []
        for json_file in sorted(os.listdir(json_folder)):
            if json_file.endswith('_combined.json'):
                with open(os.path.join(json_folder, json_file), 'r') as file:
                    data = json.load(file)
                    start_kp = data['start_kp']
                    next_kp = data['next_kp']
                    velocity = data['velocity']
                    self.data.append((start_kp, next_kp, velocity))

    def __len__(self):
        return len(self.data)

#     def __getitem__(self, idx):
#         start_kp, next_kp, velocity = self.data[idx]
#         start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0]])
#         next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0]])
#         velocity = torch.tensor(velocity)
#         return start_kp_flat, next_kp_flat, velocity
  
    def __getitem__(self, idx):
        start_kp, next_kp, velocity = self.data[idx]
        # Extract and flatten the first two elements of each keypoint in start_kp
        start_kp_flat = torch.tensor([kp for sublist in start_kp for kp in sublist[0][:2]], dtype=torch.float)
        # Extract and flatten the first two elements of each keypoint in next_kp
        next_kp_flat = torch.tensor([kp for sublist in next_kp for kp in sublist[0][:2]], dtype=torch.float)
        velocity = torch.tensor(velocity)
        return start_kp_flat, next_kp_flat, velocity
    

In [50]:
def train_test_split(src_dir):
#     dst_dir_img = src_dir + "images"
    dst_dir_anno = src_dir + "annotations"
    
    if os.path.exists(dst_dir_anno):
        print("folders exist")
    else:
        os.mkdir(dst_dir_anno)
        
#     for jpgfile in glob.iglob(os.path.join(src_dir, "*.jpg")):
#         shutil.copy(jpgfile, dst_dir_img)

    for jsonfile in glob.iglob(os.path.join(src_dir, "*_combined.json")):
        shutil.copy(jsonfile, dst_dir_anno)
        
    output = root_dir + "split_folder_reg"
    
    splitfolders.ratio(src_dir, # The location of dataset
                   output=output, # The output location
                   seed=42, # The number of seed
                   ratio=(0.8, 0.1, 0.1), # The ratio of split dataset
                   group_prefix=None, # If your dataset contains more than one file like ".jpg", ".pdf", etc
                   move=False # If you choose to move, turn this into True
                   )
    
#     shutil.rmtree(dst_dir_img)
    shutil.rmtree(dst_dir_anno)
    
    return output  

In [51]:
# class VelRegModel(nn.Module):
#     def __init__(self, input_size):
#         super(VelRegModel, self).__init__()
#         self.fc1 = nn.Linear(input_size * 2, 1024)  # Assuming start_kp and next_kp are concatenated
#         self.fc2 = nn.Linear(1024, 512)
#         self.fc3 = nn.Linear(512,256)
#         self.fc4 = nn.Linear(256,128)
#         self.fc5 = nn.Linear(128,64)
#         self.fc6 = nn.Linear(64,64)
#         self.fc7 = nn.Linear(64,6)  # Output size is 3 for velocity

#     def forward(self, start_kp, velocity):
#         x = torch.cat((start_kp, velocity), dim=1)
#         x = func.relu(self.fc1(x))
#         x = func.relu(self.fc2(x))
#         x = func.relu(self.fc3(x))
#         x = func.relu(self.fc4(x))
#         x = func.relu(self.fc5(x))
#         x = func.relu(self.fc6(x))
#         x = self.fc7(x)
#         return x

In [52]:
import torch
import torch.nn as nn
import torch.nn.functional as F

class KeypointRegressionNet(nn.Module):
    def __init__(self):
        super(KeypointRegressionNet, self).__init__()
        # Define the architecture
        self.fc1 = nn.Linear(15, 128)  # 18 keypoints + 3 velocity values
        self.fc2 = nn.Linear(128, 256)
        self.fc3 = nn.Linear(256, 256)
        
        self.fc4 = nn.Linear(128, 12)  # Output size is 18 (6 keypoints * 3 values each)

    def forward(self, start_kp, velocity):
        # Flatten start keypoints and concatenate with velocity
        x = torch.cat((start_kp, velocity), dim=1)
        
        # Forward pass through the network
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = F.relu(self.fc3(x))
        x = self.fc4(x)  # No activation function in the last layer
        return x

In [53]:
# Initialize dataset and data loader
# to generalize home directory. User can change their parent path without entering their home directory
num_epochs = 300
batch_size = 128
v = 1
root_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test_2/'
print(root_dir)
split_folder_path = train_test_split(root_dir)
dataset = KpVelDataset(root_dir)
data_loader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

# Initialize model
model = KeypointRegressionNet()  # Adjust input_size as necessary
criterion = nn.MSELoss()
optimizer = optim.Adam(model.parameters(), lr=0.005)

# Training loop
for epoch in range(num_epochs):
    for start_kp, next_kp, velocity in data_loader:
        optimizer.zero_grad()
        velocity = velocity.squeeze(1)
        print(start_kp.shape)
        print(velocity.shape)
        output = model(start_kp, velocity)
        loss = criterion(output, next_kp)
        loss.backward()
        optimizer.step()
        print("output", output)
    print(f'Epoch {epoch+1}, Loss: {loss.item()}')
    
# # Save the trained model
model_save_path = f'/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b{batch_size}_e{num_epochs}_v{v}.pth'
torch.save(model.state_dict(), model_save_path)

# model_save_path = f'/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b{batch_size}_e{num_epochs}_v{v}.pth'
# torch.save({
#     'model_state_dict': model.state_dict(),
#     'model_structure': KeypointRegressionNet()
# }, model_save_path)
# print(f"Model saved to {model_save_path}")


/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test_2/


Copying files: 3137 files [00:00, 17605.58 files/s]


torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[  0.3755, -11.9200,  -8.2594,  ...,  -3.4368,  -3.8442,  -6.5940],
        [  0.4976, -11.7770,  -8.5405,  ...,  -3.3737,  -3.9315,  -6.9842],
        [ -0.3671, -12.3275,  -7.5591,  ...,  -3.4337,  -3.6178,  -5.8184],
        ...,
        [ -0.7251, -11.2040,  -7.8257,  ...,  -6.0839,  -4.7046,  -4.3595],
        [  0.0161, -12.0585,  -8.0321,  ...,  -3.8734,  -3.8627,  -7.9975],
        [ -0.4673, -11.2488,  -8.1413,  ...,  -3.6001,  -4.5715,  -5.2706]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[42.6132, 62.1723,  7.4779,  ..., 14.5058, 23.6310, 51.8031],
        [43.3016, 63.9957,  7.3664,  ..., 14.9711, 24.2766, 53.3288],
        [38.0389, 53.6992,  6.5125,  ..., 13.6899, 18.1236, 40.7598],
        ...,
        [49.6824, 73.6856,  7.3889,  ..., 16.4269, 28.5839, 60.1466],
        [38.0840, 54.2199,  6.7092,  ..., 13.8676, 18.2255, 41.8668],
        [36.7727, 49.4853,  5.2458

torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[242.2252, 348.3666, 248.0428,  ..., 215.0430, 292.4395, 217.6120],
        [242.1182, 351.1022, 251.7318,  ..., 242.7362, 355.0414, 251.2371],
        [290.0117, 397.5147, 276.1425,  ..., 180.0630, 120.4133, 155.4583],
        ...,
        [302.7943, 407.2541, 279.7990,  ..., 187.0379,  99.0204, 157.6131],
        [247.0711, 357.4875, 256.0927,  ..., 246.3974, 355.1330, 254.4703],
        [237.1667, 348.5512, 251.5604,  ..., 230.8494, 363.6476, 239.4995]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[248.5436, 358.5568, 256.9223,  ..., 261.6209, 409.5516, 272.3589],
        [258.4626, 364.6862, 256.5467,  ..., 199.7201, 219.5354, 190.8939],
        [235.2348, 341.5971, 245.0789,  ..., 235.8137, 370.1100, 245.0183],
        ...,
        [282.4911, 392.4300, 274.2609,  ..., 192.8797, 146.1760, 171.7191],
        [247.7747, 350.7218, 247.1131,  ..., 192.5604, 228.6642, 185.3015],
    

output tensor([[249.1085, 349.1666, 247.2515, 273.5283, 238.8030, 224.6090, 247.9228,
         222.2246, 296.0775, 227.4424, 300.5702, 234.4463],
        [264.8458, 376.4427, 267.6223, 294.7419, 195.0018, 264.0314, 199.5981,
         244.7866, 188.3624, 182.3026, 192.2845, 173.8434],
        [251.1154, 358.4316, 252.8081, 276.9332, 299.1253, 222.1866, 313.8466,
         236.9031, 382.9241, 304.9104, 376.9926, 317.0641],
        [267.4573, 377.1215, 268.7354, 295.7281, 329.1194, 231.1313, 342.9965,
         248.2451, 438.8289, 298.6404, 439.5951, 308.5915],
        [262.1222, 371.3096, 260.8711, 287.9832, 176.8117, 284.2438, 174.7639,
         264.3107,  95.6527, 229.9826,  91.3046, 216.0879],
        [271.4735, 377.6129, 272.2938, 300.1266, 322.6065, 230.1946, 338.0417,
         244.6438, 443.9833, 254.4871, 453.3908, 262.7549],
        [253.7027, 369.1898, 259.3585, 280.1800, 229.4936, 215.2393, 247.9808,
         205.6098, 306.1152, 102.4073, 324.8099,  97.1747],
        [254.1222, 3

...

output tensor([[257.8856, 366.6030, 257.2303,  ..., 339.5443, 304.8707, 344.6467],
        [257.6124, 365.6554, 256.6619,  ..., 335.2393, 408.6879, 349.2357],
        [257.4346, 366.0189, 257.2564,  ..., 132.8884, 360.2340, 151.1408],
        ...,
        [256.9033, 366.3987, 257.7342,  ..., 108.8995, 232.4446,  98.8419],
        [257.4462, 365.4893, 256.5719,  ..., 334.9750, 411.7087, 351.1805],
        [256.6308, 365.4109, 257.0968,  ..., 307.5082, 364.0593, 315.8873]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[255.2652, 363.2710, 255.1297,  ..., 265.2894, 460.6373, 267.1636],
        [255.8138, 364.5020, 256.2151,  ..., 143.0138, 171.2749, 139.2089],
        [255.6890, 363.4560, 255.6875,  ..., 232.6517, 435.8209, 253.8308],
        ...,
        [256.4524, 365.4277, 257.0796,  ..., 330.4916, 393.9176, 353.2209],
        [255.6404, 363.8630, 255.5271,  ..., 140.1365, 328.1481, 136.6427],
        [255.9064, 363.7829, 255.1391,  ..., 32

output tensor([[256.8121, 365.7995, 256.4280,  ..., 151.4458, 392.3003, 163.4984],
        [257.2385, 366.1140, 257.2209,  ..., 166.2326, 138.7037, 149.9868],
        [257.3745, 366.3745, 257.2159,  ..., 110.4818, 238.1296, 105.4772],
        ...,
        [257.3005, 365.6969, 256.9513,  ..., 106.4952, 267.4440, 104.5512],
        [257.2280, 366.5179, 257.3310,  ..., 335.7138, 398.4576, 353.7637],
        [256.8236, 365.0647, 256.9737,  ..., 202.6078, 418.2978, 222.0068]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[256.6671, 366.0732, 257.0899,  ..., 137.6815, 238.2749, 139.2724],
        [257.5996, 365.9596, 257.0114,  ..., 288.2642, 316.7506, 303.9218],
        [257.3120, 366.6055, 256.8802,  ..., 152.2392, 394.9846, 166.2884],
        ...,
        [256.8379, 365.8557, 256.8689,  ..., 277.0187, 412.3674, 295.6818],
        [257.1606, 365.7147, 256.9345,  ..., 279.1821, 389.0033, 295.0756],
        [256.8311, 366.2573, 256.9854,  ..., 27

output tensor([[256.8857, 366.6058, 257.5665,  ..., 265.9156,  74.7909, 244.2948],
        [256.4882, 365.3182, 256.2921,  ..., 247.1254, 455.3861, 241.1904],
        [257.8866, 367.7670, 257.7866,  ..., 181.1011, 425.6824, 171.8695],
        ...,
        [258.1635, 366.8153, 257.0627,  ..., 146.7915, 172.9047, 139.6491],
        [256.2002, 364.4872, 256.2942,  ..., 308.8968, 359.5685, 317.9550],
        [256.5833, 365.1089, 256.8682,  ..., 313.7400, 360.1096, 328.4959]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[256.7840, 365.6386, 256.4178,  ..., 166.3054, 280.5188, 182.2681],
        [255.6017, 363.8810, 255.8969,  ..., 231.0648, 435.4175, 244.4821],
        [254.3958, 362.0671, 254.3263,  ..., 266.8609, 459.2018, 270.6960],
        ...,
        [256.9507, 365.7031, 256.5663,  ..., 166.1870, 285.0707, 171.5941],
        [256.0798, 364.6615, 256.8269,  ..., 114.4398, 275.3093,  93.5757],
        [256.9333, 365.4641, 256.4695,  ..., 17

output tensor([[257.4187, 366.4783, 257.3994,  ..., 334.3203, 352.2175, 348.6633],
        [256.8022, 365.9601, 257.0663,  ..., 341.5791, 342.4717, 346.5880],
        [257.0355, 365.8314, 256.9522,  ..., 191.4652, 342.6178, 205.6948],
        ...,
        [257.5753, 366.7289, 257.2390,  ..., 332.6862, 418.2373, 353.2808],
        [257.1115, 365.3996, 257.1691,  ..., 209.7233,  78.6340, 196.8342],
        [257.1928, 365.2842, 257.0962,  ..., 207.6553,  96.3216, 187.5170]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[256.4695, 365.5914, 256.1885,  ..., 237.9911, 342.5035, 246.2613],
        [256.2408, 365.6545, 257.1700,  ..., 173.6055, 327.3590, 194.2382],
        [256.5929, 366.3141, 257.1516,  ..., 160.3748, 271.5279, 177.2580],
        ...,
        [256.9269, 366.7060, 257.0038,  ..., 327.8416, 426.0735, 349.6355],
        [257.1547, 366.6341, 257.0962,  ..., 137.9164, 169.6005, 117.4710],
        [256.5833, 366.0258, 256.9379,  ..., 33

torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[257.0991, 366.2686, 257.2187,  ..., 259.1420,  85.7044, 239.0456],
        [257.1878, 365.7696, 257.0373,  ..., 174.0055, 285.2707, 158.3846],
        [256.2415, 366.2301, 256.6752,  ..., 118.6716, 169.5182,  97.0496],
        ...,
        [257.5593, 367.3506, 257.4276,  ..., 166.7807, 404.2133, 179.6207],
        [257.4592, 366.1657, 256.8505,  ..., 190.4445, 348.4646, 192.6750],
        [257.3581, 366.0845, 257.6296,  ..., 230.5232, 428.6717, 245.8172]],
       grad_fn=<AddmmBackward0>)
torch.Size([128, 12])
torch.Size([128, 3])
output tensor([[256.9741, 365.5286, 256.7393,  ..., 142.5862, 325.5501, 128.0860],
        [256.6971, 365.6763, 257.2019,  ..., 176.4835, 329.4633, 197.0022],
        [257.1752, 365.8211, 256.3951,  ..., 202.4978, 350.8584, 203.5629],
        ...,
        [257.5577, 365.7144, 257.0054,  ..., 298.9969, 308.2711, 304.9214],
        [256.9872, 365.5489, 256.7859,  ..., 139.7727, 323.0129, 126.4521],
    

In [76]:
def test_model(model_path, test_data_dir):
    # Load the test dataset
    test_dataset = KpVelDataset(test_data_dir)
    test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

    # Initialize the model and load the saved state
    model = KeypointRegressionNet()
    model.load_state_dict(torch.load(model_path))
    model.eval()

    # Criterion for evaluation
    criterion = nn.MSELoss()
    total_loss = 0

    # No gradient needed for evaluation
    with torch.no_grad():
        for start_kp, next_kp, velocity in test_loader:
            output = model(start_kp, velocity)
            for i in range(start_kp.size(0)):
                individual_start_kp = start_kp[i]
                individual_next_kp = next_kp[i]
                individual_velocity = velocity[i]
                predicted_next_kp = output[i]

                print("Start KP:", individual_start_kp)
                print("Next KP:", individual_next_kp)
                print("Actual Velocity:", individual_velocity)
                print("Predicted Velocity:", predicted_next_kp)
                print("-----------------------------------------")
            loss = criterion(output, next_kp)
            total_loss += loss.item()
            
    # Calculate the average loss
    avg_loss = total_loss / len(test_loader)
    print(f'Average Test Loss: {avg_loss}')

# Usage
model_path = '/home/jc-merlab/Pictures/Data/trained_models/reg_nkp_b128_e250_v0.pth'  # Update with your model path
test_data_dir = '/home/jc-merlab/Pictures/panda_data/panda_sim_vel/vel_reg_sim_test/split_folder_reg/test/annotations/'  # Update with your test data path
test_model(model_path, test_data_dir)

Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8257,
        298.1946,   1.0000, 175.8687, 277.7923,   1.0000, 240.1268, 202.5661,
          1.0000, 262.0790, 205.0822,   1.0000])
Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8260,
        298.1959,   1.0000, 175.8685, 277.7937,   1.0000, 240.1280, 202.5687,
          1.0000, 262.0802, 205.0853,   1.0000])
Actual Velocity: tensor([0.0000, 0.0000, 0.3000])
Predicted Velocity: tensor([257.7654, 366.7654,   0.9178, 257.9145, 283.0347,   1.1408, 179.7099,
        298.4261,   1.0625, 175.4932, 277.9028,   0.8915, 240.3632, 202.5495,
          1.0117, 261.5081, 204.5572,   1.1235])
-----------------------------------------
Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 179.8213,
        298.1725,   1.0000, 175.8698, 277.7691,   1.0000, 240.1633, 202.5730,
          1.0000, 262.1147, 205.0952,   1.0000])
Next KP: tensor([257.9522, 366.9199,   

Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7598,
        217.8956,   1.0000, 320.7623, 229.8525,   1.0000, 419.9565, 231.2956,
          1.0000, 442.5465, 231.8152,   1.0000])
Actual Velocity: tensor([0.0000, 0.0893, 0.0000])
Predicted Velocity: tensor([258.3449, 367.1544,   0.7209, 258.5476, 283.7431,   1.3077, 303.9985,
        219.0668,   1.1029, 320.3009, 230.5019,   0.9057, 420.4909, 232.1425,
          1.0414, 442.1325, 232.9416,   1.1690])
-----------------------------------------
Start KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7598,
        217.8956,   1.0000, 320.7623, 229.8525,   1.0000, 419.9565, 231.2956,
          1.0000, 442.5465, 231.8152,   1.0000])
Next KP: tensor([257.9522, 366.9199,   1.0000, 257.9597, 283.0131,   1.0000, 303.7659,
        217.8999,   1.0000, 320.7673, 229.8584,   1.0000, 419.9698, 230.4328,
          1.0000, 442.5634, 230.7548,   1.0000])
Actual Velocity: tensor([0.0000, 0.0893,